In [11]:
from pyraf import iraf
startup = iraf.osfn("home$pyraflogin.py")
if os.path.exists(startup):
    execfile(startup)
    del startup
    del executable   # clean up namespace

In [12]:
#Bokeh plotting
from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.models import Span, Label, Arrow, NormalHead
from bokeh.models import HoverTool, tools, ColumnDataSource, CustomJS, Slider, BoxAnnotation
from bokeh.layouts import  column, row
from bokeh.palettes import Category20_18
import re
import glob, os
from astropy.io import fits
from urllib import urlretrieve
output_notebook()

Loading BokehJS ...

In [13]:
with open('../listO.txt','r') as f:
    for lines in f:
        star = lines.split(',')[0]
        url= lines.split(',')[1]
        name = url.split('/')[-1]
        if not os.path.isfile(name.strip()):
            urlretrieve(url,name.strip())
        #print(url)

# Bokeh Plotting

In [14]:
#plot parameters
colors = 100*Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (0,40)
p =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
p.add_tools(hover2)


for index,file in enumerate(glob.glob("spec*.fits")):
    
    if index < 10:
        ob = fits.open(file)
        dataob = ob[1].data

        x=10**(dataob['loglam'])
        y=dataob['flux']

        #If you want to have the name and not the spectra type change legend=name
        t = p.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
               line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])
        #This is a very ideficient way to have the colors in the legend to show up by default. 
    #    t2 = p.line(x=x[0],y=y[0],color=colors[index], line_alpha=1.0, 
    #           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=1.,muted_color=colors[index])





    #    t = p.line(x=10**(dataob['loglam']),y=dataob['model'], line_alpha=0.0, 
    #           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),color=colors[i],muted_color=colors[i])
    #    #This is a very ideficient way to have the colors in the legend to show up by default. 
    #    t2 = p.line(x=10**(dataob['loglam']),y=dataob['model'], line_alpha=1.0, 
    #           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=1.,color=colors[i],muted_color=colors[i])

    else:
        pass
    
    
    
p.legend.location = "top_left"
p.legend.click_policy="mute"
show(p)

In [15]:
ob[1].header


XTENSION= 'BINTABLE'           / binary table extension                         
BITPIX  =                    8 / array data type                                
NAXIS   =                    2 / number of array dimensions                     
NAXIS1  =                   32 / length of dimension 1                          
NAXIS2  =                 3843 / length of dimension 2                          
PCOUNT  =                    0 / number of group parameters                     
GCOUNT  =                    1 / number of groups                               
TFIELDS =                    8 / number of table fields                         
TTYPE1  = 'flux    '                                                            
TFORM1  = 'E       '                                                            
TTYPE2  = 'loglam  '                                                            
TFORM2  = 'E       '                                                            
TTYPE3  = 'ivar    '        

# Plotting the model not the data

In [16]:
#plot parameters
colors = 100*Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (-.5,.5)
p =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
p.add_tools(hover2)


#os.chdir("/mydir")
for index,file in enumerate(glob.glob("spec*.fits")):
    if index <10:
        ob = fits.open(file)
        dataob = ob[1].data

        x=10**(dataob['loglam'])
        y=dataob['model']

        #If you want to have the name and not the spectra type change legend=name
        t = p.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
               line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])

    
    else:
        pass
    
p.legend.location = "top_left"
p.legend.click_policy="mute"
show(p)

# Table to IRAF 

To find a gaussian can use the iraf routine [fitprofs](http://stsdas.stsci.edu/cgi-bin/gethelp.cgi?fitprofs). To use this need to convert the SDSS tables to IRAF image spectra. 

In [18]:
#Parametest for the fit:
def find_nearest(array,value):
    idx = (np.abs(array-value)).argmin()
    return idx, array[idx]

def isDigit(x):
    try:
        float(x)
        return True
    except ValueError:
        return False
    
def gaussian(x, mu, sig,core):
    return core*np.exp(-np.power(x - mu, 2.) / (2 * np.power(sig, 2.)))


#Error
eeqwgs = []
errorparam = []
errorestimate = True


#plot parameters
colors = Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (.0001,.001)
pl =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
pl.add_tools(hover2)




for index,filename in enumerate(glob.glob("spec*.fits")):
    
    if index < 10:    
        #import fits
        ob = fits.open(filename)
        #Get data and save wavelenft in x, and flux on y
        dataob = ob[1].data
        x = 10**(dataob['loglam'])
        y = dataob['model']

        #save to a .txt file
        namenewfits = '{name}.txt'.format(name=filename.split('.')[0])
        with open(namenewfits,'w') as file:
            for i in zip(x,y):
                file.write('{}\t{}\n'.format(i[0],i[1]))
        #Create fits file from text file interpolation. 
        iraffitsname = 'iraf'+filename.split('.')[0]
        if os.path.exists(iraffitsname+'.fits'):
            os.remove(iraffitsname+'.fits')

        iraf.noao.onedspec()
        iraf.dataio()
        iraf.noao.onedspec.rspectext(namenewfits,iraffitsname,dtype='interp')



        line = [8543,8598.,6562]
        regionfit = [[8520,8560],[8582,8609],[6550,6575]]

        #Initialize files log and lines
        ! echo '' > fited.log


        for lines in zip(line,regionfit):
            regionf = "{} {}".format(lines[1][0],lines[1][1])
            #wavelenght
            xlimns = [find_nearest(x,i)[0] for i in lines[1]    ]
            wavex = x[xlimns[0]:xlimns[1]]
            lineszero = lines[0]
            ! echo '$lineszero' > lines.lines

            filename = iraffitsname

            if errorestimate == True:        
                iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                              fitbackground= 'yes', 
                              logfile='fited.log'
                              ,nerrsample='100',sigma0='4',invgain='4')
            else:
                iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                              fitbackground= 'yes', 
                              logfile='fited.log')



            #Plotting the gaussian
            #Find in log file  
            npattern = re.compile('[-\d.]+')
            npattern2 = re.compile('[-\d.E?]+')

            gparameters=[]
            with open('fited.log','r') as file:
                for lines in file:

                    if '(' not in lines:
                        temp = npattern2.findall(lines)
                        if 'INDEF' in lines:
                            gparameters.append(7*[0])
                    else:
                        errorparam.append(npattern2.findall(lines))

                    if len(temp) == 7 and all(isDigit(i) for i in temp) and 'INDEF' not in lines:
                        gparameters.append(temp)

            #gaussian
            if len(gparameters) > 0:
                gparamfinal = [ float(i) for i in gparameters[-1] ]
                centerg, contg, fluxg, eqwg, coreg, fwhmg, fwhml = gparamfinal
                yg = gaussian(wavex,centerg,fwhmg/2.3538,coreg) + contg


            if errorestimate == True:
                errorparamfinal = [ float(i) for i in errorparam[-1] ]
                print(gparamfinal)
                print(errorparamfinal)

                #Plot
                #sourceg = ColumnDataSource(data=dict(x=wavex,y=yg))
                #pl.line(wavex,yg,color=colors[index], line_alpha=1.0, 


                        #color=colors[index], line_alpha=1.0, 
                       #line_width=4,muted_alpha=0.,muted_color=colors[index])
                pl.line(wavex,yg,color='red', line_alpha=1., 
                    line_width=5,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])



        #If you want to have the name and not the spectra type change legend=name
                t = pl.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
                       line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])



                message = 'type:{sclass},center:{cent},eqw:{eq}({eqer})'


                eeqwgs.append([message.format(sclass = ob[2].data['SUBCLASS'][0]+str(index),
                               cent = centerg
                               ,eq = eqwg
                               ,eqer = errorparamfinal[3])])

    else:
        pass

pl.legend.location = "top_left"
pl.legend.click_policy="mute"

show(pl)           

# Jan 28 19:21 irafspec-0268-51633-0008 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8539.008  4.960271   5.20434    -1.049  0.122468     39.92        0.
 (2307.22) (34.9221) (3.567E6) (  2105.) (114.844) ( 33617.) (     0.)
[8539.008, 4.960271, 5.20434, -1.049, 0.122468, 39.92, 0.0]
[2307.22, 34.9221, 3567000.0, 2105.0, 114.844, 33617.0, 0.0]
# Jan 28 19:21 irafspec-0268-51633-0008 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8592.879  4.855231  0.829035   -0.1708 0.0949525     8.202        0.
 (1107.78) (6.89665) (4550.43) (  191.8) (39.0828) (  420.2) (     0.)
[8592.879, 4.855231, 0.829035, -0.1708, 0.0949525, 8.202, 0.0]
[1107.78, 6.89665, 4550.43, 191.8, 39.0828, 420.2, 0.0]
# Jan 28 19:21 irafspec-0268-51633-0008 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#

/home/mmarcano/anaconda3/envs/iraf27/lib/python2.7/site-packages/ipykernel_launcher.py:14: RuntimeWarning: divide by zero encountered in divide
  


# Jan 28 19:21 irafspec-0269-51910-0534 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8595.485 -0.047313 -0.010896     INDEF -0.002737      3.74        0.
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[72.8623, 3.1005, 3897.88, 64.55, 51.6403, 56.83, 0.0]
# Jan 28 19:21 irafspec-0269-51910-0534 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  6564.295 -0.016947 -0.198415     INDEF -0.007135     26.13        0.
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[72.8623, 3.1005, 3897.88, 64.55, 51.6403, 56.83, 0.0]
# Jan 28 19:21 irafspec-0270-51909-0331 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8537.669  -0.07471 0.0252081     INDEF 0.0029342     8.071        0.
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[72.8623, 3.1005, 3897.

# Jan 28 19:22 irafspec-0277-51908-0548 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8541.299 0.0288843 -0.099892     3.458 -0.003356     27.96        0.
 (47210.4) (18.5341) (1.263E6) ( 13098.) (56.2409) (175730.) (     0.)
[8541.299, 0.0288843, -0.099892, 3.458, -0.003356, 27.96, 0.0]
[47210.4, 18.5341, 1263000.0, 13098.0, 56.2409, 175730.0, 0.0]
# Jan 28 19:22 irafspec-0277-51908-0548 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8541.139 0.8707897  -1783.22     2048. -0.842877     1988.        0.
 (350994.) (19478.5) (1.78E12) (2.060E7) (19697.5) (9.740E7) (     0.)
[8541.139, 0.8707897, -1783.22, 2048.0, -0.842877, 1988.0, 0.0]
[350994.0, 19478.5, 1780000000000.0, 20600000.0, 19697.5, 97400000.0, 0.0]
# Jan 28 19:22 irafspec-0277-51908-0548 - Ap 1: 
# Nfit=1, background=yes, positions=al

In [7]:
eeqwgs

[['type:O0,center:8539.008,eqw:-1.049(2105.0)'],
 ['type:O0,center:8592.879,eqw:-0.1708(191.8)'],
 ['type:O0,center:6564.906,eqw:1.237(64.55)'],
 ['type:O1,center:0.0,eqw:0.0(64.55)'],
 ['type:O1,center:0.0,eqw:0.0(64.55)'],
 ['type:O1,center:0.0,eqw:0.0(64.55)'],
 ['type:O2,center:0.0,eqw:0.0(64.55)'],
 ['type:O2,center:0.0,eqw:0.0(64.55)'],
 ['type:O2,center:6562.207,eqw:-26.2(353.2)'],
 ['type:O3,center:8548.734,eqw:-0.6589(3741.0)'],
 ['type:O3,center:8599.773,eqw:0.498(4785.0)'],
 ['type:O3,center:6565.903,eqw:7.052(1355.0)'],
 ['type:O4,center:8548.856,eqw:1.011(788.7)'],
 ['type:O4,center:8598.727,eqw:1.6(1478.0)'],
 ['type:O4,center:6561.401,eqw:93.91(1478.0)'],
 ['type:O5,center:0.0,eqw:0.0(1478.0)'],
 ['type:O5,center:0.0,eqw:0.0(1478.0)'],
 ['type:O5,center:6560.271,eqw:8.526(2592.0)'],
 ['type:O6,center:8548.749,eqw:0.5276(3278.0)'],
 ['type:O6,center:8597.623,eqw:-1.584(74501.0)'],
 ['type:O6,center:6565.688,eqw:-2.816(4174.0)'],
 ['type:O7,center:8533.206,eqw:-2.207(5234.

In [41]:
#! /usr/bin/env python

# Copyright (c) 2012 Victor Terron. All rights reserved.
# Institute of Astrophysics of Andalusia, IAA-CSIC
#
# This file is part of LEMON.
#
# LEMON is free software: you can redistribute it and/or modify
# it under the terms of the GNU General Public License as published by
# the Free Software Foundation, either version 3 of the License, or
# (at your option) any later version.
#
# This program is distributed in the hope that it will be useful,
# but WITHOUT ANY WARRANTY; without even the implied warranty of
# MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE. See the
# GNU General Public License for more details.
#
# You should have received a copy of the GNU General Public License
# along with this program. If not, see <http://www.gnu.org/licenses/>.

from __future__ import with_statement

""" Just a shadow of what the actual setup.py will look like, this simple
script, when run, creates the IRAF login script (login.cl file) and the user
parameters directory (uparm) in the directory where LEMON is installed. This
directory is automatically detected as it is assumed to be the same in which
this file is located, so it does not depend on where it is executed from.

"""

import os
import os.path
import errno
import shutil
import subprocess

MKIRAF_BIN = 'mkiraf'
TERM_TYPE = 'xgterm'
LOGIN_FILE = 'login.cl'
UPARM_DIR = 'uparm'
PYRAF_CACHE = 'pyraf'


def mkiraf(path):
    """ Create the IRAF login script and the uparm directory.

    This function implements a high-level wrapper around IRAF's mkiraf, which
    initializes the IRAF login script and the user parameters directory in the
    path given as input. Any existing login script or uparm directory is
    silently overwritten, although mkiraf makes a backup of the former by
    appending '.OLD' to its name. In this manner, the original login script
    'login.cl' becomes 'login.cl.OLD'.

    The login script that this function creates chooses 'xgterm' as its
    terminal type. It is usually the best choice, being a xterm-like terminal
    program written specifically to work with IRAF. Note that, although we are
    required to choose a terminal type when mkiraf is run, LEMON never needs
    to use it.

    """

    os.chdir(path)

    # Avoid having to answer the "Initialize uparm? (y|n):" question
    if os.path.exists(UPARM_DIR):
        shutil.rmtree(UPARM_DIR)

    # mkiraf reads the terminal type ("Enter terminal type:") from the user,
    # not accepting it as a command line argument. Thus, we need to use a pipe
    # to send the terminal type to mkiraf's stdin.
    args = [MKIRAF_BIN]
    p = subprocess.Popen(args, stdin = subprocess.PIPE, stdout = subprocess.PIPE)
    p.communicate(input = TERM_TYPE)

    if p.returncode:
        msg = "execution of %s failed" % MKIRAF_BIN
        raise subprocess.CalledProcessError(p.returncode, args)

    with open(LOGIN_FILE, 'rt') as fd:
        for line in fd:
            splitted = line.split()
            if len(splitted) == 2:
                if splitted[0] == 'stty':
                    if splitted[1] == TERM_TYPE:
                        break
                    else:
                        msg = "terminal type wasn't set correctly"
                        raise ValueError(msg)
        else:
            msg = "terminal type not defined in %s" % LOGIN_FILE
            raise ValueError(msg)

def mkdir_p(path):
    """ Create a directory, give no error if it already exists.

    This implements the functionality of Unix `mkdir -p`, creating a
    directory but without giving any error if it already exists and
    making parent directories as needed.
    [URL] http://stackoverflow.com/a/600612/184363

    """

    try:
        os.mkdir(path)
    except OSError as exc: # Python >2.5
        if exc.errno == errno.EEXIST and os.path.isdir(path):
            pass
        else:
            raise


if __name__ == "__main__":

    pyraf_cache_path = PYRAF_CACHE
    mkdir_p(pyraf_cache_path)
    print 'done.'



done.


In [ ]:
! pyth